## 1 Setup BART
This notebook is designed to run on a local system. It uses the python kernel, however, almost all commands use the `%%bash` cell magic to be executed in a `bash` subshell.

We will use BART version 0.9.00.. For more information check the announcement on our [mailing list](https://lists.eecs.berkeley.edu/sympa/arc/mrirecon/2023-12/msg00000.html).


This version has been archived at CERN as:  

BART: version 0.9.00 (2023) DOI:10.5281/zenodo.10277939

### 1.1 Local Usage
- Install bart from its [github repository](https://github.com/mrirecon/bart)
- Set the `BART_TOOLBOX_PATH` to the BART directory and add it to the `PATH`

```bash
export BART_TOOLBOX_PATH=/path/to/bart  
export PATH=$BART_TOOLBOX_PATH:$PATH
```

Although the simplest way to call the BART CLI tools is from a terminal, there are also wrapper functions that allow the tools to be used from Matlab and Python. These are located under the `$BART_TOOLBOX_PATH/matlab` and `$BART_TOOLBOX_PATH/python` directories.

In [1]:
import os
os.environ['DEMO'] = '1'
os.environ['DEMO_INSTALL'] = '0'

### 1.2 Clone and compile BART v0.9.00
We clone BART into the current working directory of this notebook and delete any previous installation in this directory.

In [2]:
%%bash

# Clone Bart
if [ 1 -eq $DEMO_INSTALL ]; then

    [ -d bart ] && rm -r bart
    git clone https://github.com/mrirecon/bart/ bart &> /dev/null

    cd bart

    make -j32 &> /dev/null
else
    echo skipped .. DEMO_INSTALL=$DEMO_INSTALL
fi

skipped .. DEMO_INSTALL=0


### 1.3 Add BART to PATH variable

We add the BART directory to the PATH variable and include the python wrapper for reading *.cfl files:

In [3]:
import os
import sys

os.environ['BART_TOOLBOX_PATH']=os.getcwd()+"/bart/"
os.environ['PATH'] = os.environ['BART_TOOLBOX_PATH'] + ":" + os.environ['PATH']
sys.path.append(os.environ['BART_TOOLBOX_PATH'] + "/python/")
os.environ['DEBUG_LEVEL'] = '2'
os.environ['BART_DEBUG_LEVEL'] = '2'

Check BART setup:

In [4]:
%%bash

echo "# The BART used in this notebook:"
which bart
echo "# BART version: "
bart version

# The BART used in this notebook:
/home/jupyter-jupfi/esmrmb-educational/bart//bart
# BART version: 
v0.9.00-466-gb3be61a


In [5]:
import os
import subprocess

# Function to execute shell command within Jupyter notebook
def run_command(command):
    process = subprocess.Popen(command, shell=True, stdout=subprocess.PIPE, stderr=subprocess.PIPE)
    stdout, stderr = process.communicate()
    return process.returncode, stdout.decode(), stderr.decode()

# Check if venv exists
venv_path = './venv'
if not os.path.exists(venv_path):
    # Create venv if it doesn't exist
    print("Creating virtual environment...")
    result, out, err = run_command('python3 -m venv venv')
    if result != 0:
        print(f"Error creating virtual environment: {err}")

else:
    print("Virtual environment already exists.")

# Activate the virtual environment and install packages
activate_command = '. venv/bin/activate && pip install numpy scipy matplotlib'

print("Activating virtual environment and installing packages...")
result, out, err = run_command(activate_command)
if result != 0:
    print(f"Error activating virtual environment or installing packages: {err}")
else:
    print(out)

Virtual environment already exists.
Activating virtual environment and installing packages...



In [6]:
# Python Stuff
from bart import bart
import cfl

In [7]:
# Bart viewer
import numpy as np
import matplotlib.pyplot as plt
from matplotlib import cm
from mpl_toolkits.axes_grid1 import make_axes_locatable
import ipywidgets as widgets
from IPython.display import display
from traitlets import List, Bool

class DimensionSelector(widgets.HBox):
    value = List(Bool()).tag(sync=True)

    def __init__(self, n_dims):
        self.checkboxes = [widgets.Checkbox(value=i<2, description=f'Dim {i}') for i in range(n_dims)]
        super().__init__(self.checkboxes)
        for cb in self.checkboxes:
            cb.observe(self.on_change, 'value')
        self.value = [cb.value for cb in self.checkboxes]

    def on_change(self, change):
        selected = [cb for cb in self.checkboxes if cb.value]
        if len(selected) > 2:
            selected[0].value = False
        self.value = [cb.value for cb in self.checkboxes]

def interactive_bart_plot(data, cmap='gray', cbar_label='', mag=True, fsize=10):
    data = np.array(data)
    if mag:
        data = np.abs(data)

    def update_plot(plot_dims, interpolation, **slice_values):
        plt.clf()
        selected_dims = [i for i, sel in enumerate(plot_dims) if sel]
        if len(selected_dims) != 2:
            plt.text(0.5, 0.5, 'Please select exactly two dimensions for plotting', 
                     ha='center', va='center', fontsize=12)
            plt.axis('off')
        else:
            # Create a slice object for indexing
            index = [slice(None)] * data.ndim
            for i in range(data.ndim):
                if i not in selected_dims:
                    index[i] = slice_values[f'slice_dim{i}']
            
            # Extract the 2D slice to plot
            plot_data = data[tuple(index)]
            
            fig, ax1 = plt.subplots(figsize=(fsize, fsize))
            im = ax1.imshow(plot_data, interpolation=interpolation, cmap=cmap)
            
            divider = make_axes_locatable(ax1)
            cax = divider.append_axes("right", size="5%", pad=0.05)
            cbar = plt.colorbar(im, cax=cax)
            cbar.set_label(cbar_label)
            
            ax1.set_title(f'Dimensions: {selected_dims}, Interpolation: {interpolation}')
            ax1.set_axis_off()
        plt.show()

    dim_selector = DimensionSelector(data.ndim)
    
    def create_slice_widget(i):
        widget = widgets.IntText(value=0, description=f'Slice Dim {i}:', 
                                 layout=widgets.Layout(width='200px'))
        
        def on_value_change(change):
            if change['new'] < 0:
                widget.value = 0
            elif change['new'] >= data.shape[i]:
                widget.value = data.shape[i] - 1
        
        widget.observe(on_value_change, names='value')
        return widget

    slice_widgets = {f'slice_dim{i}': create_slice_widget(i) for i in range(data.ndim)}
    
    interpolation_options = ['nearest', 'bilinear', 'bicubic', 'spline16', 'spline36', 'hanning', 'hamming', 'hermite', 'kaiser', 'quadric', 'catrom', 'gaussian', 'bessel', 'mitchell', 'sinc', 'lanczos']
    interpolation_widget = widgets.Dropdown(
        options=interpolation_options,
        value='nearest',
        description='Interpolation:',
        layout=widgets.Layout(width='200px')
    )
    
    slice_ui = widgets.VBox(list(slice_widgets.values()))
    ui = widgets.VBox([dim_selector, interpolation_widget, slice_ui])
    
    controls = {'plot_dims': dim_selector, 'interpolation': interpolation_widget, ** slice_widgets}
    out = widgets.interactive_output(update_plot, controls)
    
    display(ui, out)



In [8]:
# BartIO (used for bitmask)
import io
import contextlib

def bartIO(*args, **kwargs):
    buffer = io.StringIO()

    with contextlib.redirect_stdout(buffer):
        bart(*args, **kwargs)

    return buffer.getvalue()

In [9]:
# Testing the viewer
bart_phantom = bart(1, 'phantom -x 256 -B').T
interactive_bart_plot(bart_phantom)


Output()

## 2. Reading in the data

In [10]:
import scipy.io as sio

rawName = 'T2_CPMG.mat'
mat_data_0=sio.loadmat(rawName)

# Format: sampled, # kSpace [kRd, kPh, kSl, kSpace_echo_1, kSpace_echo_2, ..., kSpace_echo_nETL] (102400, 23)
# So the first three are the coordinates of the kspace, and the rest are the echoes

kSpaces3D = mat_data_0['kSpaces3D']
# self.mapVals['sampled'] = np.concatenate((kRD, kPH, kSL, dataAll_sampled), axis=1)

# nReadout, nPhase, nSlice
nPoints = (80, 80, 16)

echo_train_length = mat_data_0['kSpaces3D'].shape[1] - 3 # Because the first 3 are kRD, kPH, kSL -> should give 20
print(f"Echo train length: {echo_train_length}")

echo_spacing = mat_data_0['echoSpacing'][0][0]
print(f"Echo spacing: {echo_spacing} ms")

k_readout = kSpaces3D[:, 0]
k_phase = kSpaces3D[:, 1]
k_slice = kSpaces3D[:, 2]

# The rest of the data is the echoes
echos = kSpaces3D[:, 3:]

# Reshape the kspace data for bart
kSpace = echos.reshape(nPoints[2], nPoints[1], nPoints[0], echo_train_length)

print(kSpace.shape)

Echo train length: 20
Echo spacing: 10 ms
(16, 80, 80, 20)


In [11]:
interactive_bart_plot(kSpace)


Output()

### 2.1 Data Exploration

In [12]:
print("kSpace dimensions:")
bart(0, 'show -m', kSpace)

DIM_X = 80
DIM_Y = 80
DIM_Z = 16

kSpace dimensions:
Type: complex float
Dimensions: 16
AoD:	16	80	80	20	1	1	1	1	1	1	1	1	1	1	1	1


In [13]:
# Correct dimension
kSpace_transposed = bart(1, 'transpose 0 2', kSpace)
kSpace_transposed = bart(1, 'transpose 3 5', kSpace_transposed)
print("New Shape:")
kSpace_transposed.shape

New Shape:


(80, 80, 16, 1, 1, 20)

### 2.2 FFT

We have three dimensional data so we perform the fft along the first three dimension. 

In [14]:
bitmask= bartIO(0, "bitmask 0 1 2")

In [15]:
fft = bart(1, f'fft -i {int(bitmask)}', kSpace_transposed)

In [16]:
interactive_bart_plot(fft)

Output()

In [17]:
echo_times = np.linspace(10, 200, num=echo_train_length) 
echo_times *= 0.001
print(f'Echo times:\n {echo_times}')
echo_times_final = bart(1, 'transpose 0 5', echo_times)

Echo times:
 [0.01 0.02 0.03 0.04 0.05 0.06 0.07 0.08 0.09 0.1  0.11 0.12 0.13 0.14
 0.15 0.16 0.17 0.18 0.19 0.2 ]


In [18]:
! bart mobafit -h

Usage: mobafit [-T] [-I] [-L] [-G] [-D] [-m d] [-a] [-i d] [-g] [-B <file>] [--init [f:]*f] [--scale [f:]*f] [--min-flag d] [--max-flag d] [--max-mag-flag d] [--min [f:]*f] [--max [f:]*f] <enc> <echo/contrast images> [<coefficients>] 

Pixel-wise fitting of physical signal models.

-T                      Multi-Echo Spin Echo: f(M0, R2) = M0 * exp(-t * R2)
-I                      Inversion Recovery: f(M0, R1, c) =  M0 * (1 - exp(-t * R1 + c))
-L                      Inversion Recovery Look-Locker
-G                      MGRE
-D                      diffusion
-m model                Select the MGRE model from enum { WF = 0, WFR2S, WF2R2S, R2S, PHASEDIFF } [default: WFR2S]
-a                      fit magnitude of signal model to data
-i iter                 Number of IRGNM steps
-g                      use gpu
-B file                 temporal (or other) basis
--init [f:]*f           Initial values of parameters in model-based reconstruction
--scale [f:]*f          Scaling
--min-flag flag

In [19]:
R2 = bart(1, 'mobafit -T', echo_times_final, fft)

In [20]:
R2.shape

(80, 80, 16, 1, 1, 1, 2)

In [21]:
interactive_bart_plot(R2)
# Oh noes! The fit  doesn't work :(

Output()

In [22]:
! bart threshold -h

Usage: threshold [-H] [-W] [-L] [-D] [-B] [-M] [-j d] [-b d] lambda <input> <output> 

Perform (soft) thresholding with parameter lambda.

-H              hard thresholding
-W              daubechies wavelet soft-thresholding
-L              locally low rank soft-thresholding
-D              divergence-free wavelet soft-thresholding
-B              thresholding with binary output where (val>lambda)
-M              thresholding with binary output where (val<lambda)
-j bitmask      joint soft-thresholding
-b blocksize    locally low rank block size
-h              help


In [23]:
MAX_T2 = 1

T2 = bart(1, 'invert', R2)

mask = bart(1, f'threshold -M {MAX_T2}', T2)

In [24]:
T2_masked = T2 * mask

In [25]:
interactive_bart_plot(T2_masked, cmap='viridis') #(yay)

Output()

## 2.3 PICS Reco Fully Sampled Data

In [75]:
ecalib_full = bart(1, 'ecalib -m1', kSpace_transposed)

In [76]:
interactive_bart_plot(ecalib_full)

Output()

In [77]:
! bart pics -h

Usage: pics [-l ...] [-r f] [-R ...] [-c] [-s f] [-i d] [-t <file>] [-n] [-N] [-g] [--gpu-gridding] [-p <file>] [--precond] [-b d] [-e] [-W <file>] [-d d] [-u f] [-C d] [-f f] [-I,--ist] [--fista] [--eulermaruyama] [-m,--admm] [-a,--pridu] [-w f] [-S] [--shared-img-dims d] [-K] [-B <file>] [-P f] [-M] [-U,--lowmem] [--no-toeplitz] [--psf_export <file>] [--psf_import <file>] [--wavelet <string>] [--mpi d] [--fista_pqr f:f:f] [--fista_last] <kspace> <sensitivities> <output> 

Parallel-imaging compressed-sensing reconstruction.


-l1/-l2                    toggle l1-wavelet or l2 regularization.
-r lambda                  regularization parameter
-R <T>:A:B:C               generalized regularization options (-Rh for help)
-c                         real-value constraint
-s step                    iteration stepsize
-i iter                    max. number of iterations
-t file                    k-space trajectory
-n                         disable random wavelet cycle spinning
-N          

In [78]:
bitmask = bartIO(0, 'bitmask 5')

REGULARIZATION = 3e-2
ITERATIONS=50

pics_fully = bart(1, f'pics -RI:{int(bitmask)}:{REGULARIZATION} -i{ITERATIONS} -S', kSpace_transposed, ecalib_full)
# pics_fully = bart(1, f'pics -l1 -r{REGULARIZATION} -i{ITERATIONS} -S', kSpace_transposed, ecalib_full)

Size: 2048000 Samples: 2047999 Acc: 1.00
l1 regularization: 0.030000
Regularization terms: 1, Supporting variables: 0
FISTA
Total Time: 2.629528


In [79]:
# Plot the pics reco
interactive_bart_plot(pics_fully)

Output()

In [80]:
R2_pics = bart(1, 'mobafit -T', echo_times_final, pics_fully)

MAX_T2 = 1

T2_pics = bart(1, 'invert', R2_pics)

mask_pics = bart(1, f'threshold -M {MAX_T2}', T2_pics)

T2_pics_masked = T2_pics * mask_pics

interactive_bart_plot(T2_pics_masked, cmap='viridis')

Output()

## 3.1 Undersampling Poisson ky - kz

In [81]:
ACC_Y=2
ACC_Z=2
CENTER=16

poisson_mask = bart(1, f'poisson -Y {kSpace_transposed.shape[1]} -Z {kSpace_transposed.shape[2]} -y {ACC_Y} -z {ACC_Z} -C {CENTER} -e')

points: 451, grid size: 80x16x(pi/4) = 1005 (R = 2.229068)


In [82]:
interactive_bart_plot(poisson_mask)

Output()

In [83]:
# Apply the mask
kSpace_poisson = bart(1, 'fmac', poisson_mask, kSpace_transposed)
interactive_bart_plot(kSpace_poisson)

Output()

In [84]:
! bart nlinv -h

Usage: nlinv [-i d] [-d d] [-c] [-N] [-m d] [-U] [-f f] [-p <file>] [-t <file>] [-B <file>] [-I <file>] [-g] [-S] [--lowmem] [-x,--dims d:d:d] [--sens-dims d:d:d] [--real-time] [--fast] <kspace> <output> [<sensitivities>] 

Jointly estimate image and sensitivities with nonlinear
inversion using {iter} iteration steps. Optionally outputs
the sensitivities.

-i iter              Number of Newton steps
-d level             Debug level
-c                   Real-value constraint
-N                   Do not normalize image with coil sensitivities
-m nmaps             Number of ENLIVE maps to use in reconstruction
-U                   Do not combine ENLIVE maps in output
-f FOV               restrict FOV
-p file              pattern / transfer function
-t file              kspace trajectory
-B file              temporal (or other) basis
-I file              File for initialization
-g                   use gpu
-S                   Re-scale image after reconstruction
--lowmem             Use lo

In [85]:
#Nlinv
ITERATIONS=25
nlinv_poisson = bart(1, f'nlinv -i{ITERATIONS} -x 80:80:16 -S -d4', kSpace_poisson) # This takes some time (5min)...


Model created (Cartesian):
kspace:  [ 80  80  16   1   1  20   1   1   1   1   1   1   1   1   1   1 ]
images:  [ 80  80  16   1   1  20   1   1   1   1   1   1   1   1   1   1 ]
coils:   [ 80  80  16   1   1  20   1   1   1   1   1   1   1   1   1   1 ]
pattern: [ 80  80  16   1   1  20   1   1   1   1   1   1   1   1   1   1 ]
coilimg: [ 80  80  16   1   1  20   1   1   1   1   1   1   1   1   1   1 ]

Scaling: 0.349091
Step: 0, Res: 100.000001
	 cg:   0
Step: 1, Res: 99.959831
	 cg:   0
Step: 2, Res: 99.998280
	 cg:   0
Step: 3, Res: 99.999653
	 cg:   0
Step: 4, Res: 99.999687
	 cg:   0
Step: 5, Res: 99.998778
	 cg:   0
Step: 6, Res: 99.977362
	 cg:   1
Step: 7, Res: 99.069636
	 cg:   2
Step: 8, Res: 72.770714
	 cg:   8
Step: 9, Res: 60.890033
	 cg:   1
Step: 10, Res: 43.049279
	 cg:  33
Step: 11, Res: 136.236493
	 cg:   0
Step: 12, Res: 44.616604
	 cg:   1
Step: 13, Res: 14.514742
	 cg:  16
Step: 14, Res: 23.674170
	 cg:   1
Step: 15, Res: 4.198526
	 cg:   6
Step: 16, Res: 0.31199

In [86]:
R2_nlinv_poisson = bart(1, 'mobafit -T', echo_times_final, nlinv_poisson)

MAX_T2 = 1

T2_nlinv_poisson = bart(1, 'invert', R2_nlinv_poisson)

mask_nlinv_poisson = bart(1, f'threshold -M {MAX_T2}', T2_nlinv_poisson)

T2_nlinv_poisson_masked = T2_nlinv_poisson * mask_nlinv_poisson

interactive_bart_plot(T2_nlinv_poisson_masked, cmap='viridis')

Output()

## 3.2 Uniform Undersampling
Using bart upat - same pattern for every echo.

In [87]:
ACC_Y=4
ACC_Z=4
CENTER=9

upat_mask = bart(1, f'upat -Y {kSpace_transposed.shape[1]} -Z {kSpace_transposed.shape[2]} -y {ACC_Y} -z {ACC_Z} -c {CENTER}')

interactive_bart_plot(upat_mask)

Output()

In [88]:
# Apply the mask
kSpace_upat = bart(1, 'fmac', upat_mask, kSpace_transposed)
interactive_bart_plot(kSpace_upat)

Output()

In [89]:
# PICS reco because its faster - using ecalib from fully sampled data?

bitmask = bartIO(0, 'bitmask 5')

REGULARIZATION = 10e-2
ITERATIONS=50

pics_upat = bart(1, f'pics -RI:{int(bitmask)}:{REGULARIZATION} -i{ITERATIONS} -S', kSpace_upat, ecalib_full)

Size: 2048000 Samples: 531200 Acc: 3.86
l1 regularization: 0.100000
Regularization terms: 1, Supporting variables: 0
FISTA
Total Time: 2.628610


In [90]:
R2_pics_upat = bart(1, 'mobafit -T', echo_times_final, pics_upat)

MAX_T2 = 1

T2_pics_upat = bart(1, 'invert', R2_pics_upat)

mask_pics_upat = bart(1, f'threshold -M {MAX_T2}', T2_pics_upat)

T2_pics_upat_masked = T2_pics_upat * mask_pics_upat

interactive_bart_plot(T2_pics_upat_masked, cmap='viridis')

Output()

### 3.3.1 Uniform Undersampling
With varying patterns along the echos

In [91]:
%%bash
cat << 'EOF' > create_pattern.sh
#!/bin/bash

create_pattern() {
    # Default values for parameters
    local R_Y=4
    local R_Z=1
    local Y=80
    local Z=16
    local N_ECHO=20
    local CENTER_SIZE=16
    local OUTPUT_NAME='upat_combined_new'

    # Parse named arguments
    while [[ "$#" -gt 0 ]]; do
        case $1 in
            -R_Y) R_Y="$2"; shift 2 ;;
            -R_Z) R_Z="$2"; shift 2 ;;
            -Y) Y="$2"; shift 2 ;;
            -Z) Z="$2"; shift 2 ;;
            -N_ECHO) N_ECHO="$2"; shift 2 ;;
            -CENTER_SIZE) CENTER_SIZE="$2"; shift 2 ;;
            -OUTPUT_NAME) OUTPUT_NAME="$2"; shift 2 ;;
            *) echo "Unknown parameter passed: $1"; return 1 ;;
        esac
    done

    # Check if all required parameters are provided
    if [ -z "$R_Y" ] || [ -z "$R_Z" ] || [ -z "$Y" ] || [ -z "$Z" ] || [ -z "$N_ECHO" ] || [ -z "$CENTER_SIZE" ] || [ -z "$OUTPUT_NAME" ]; then
        echo "Usage: create_pattern -R_Y <value> -R_Z <value> -Y <value> -Z <value> -N_ECHO <value> -CENTER_SIZE <value> -OUTPUT_NAME <value>"
        return 1
    fi

    # Create a temporary directory
    local TMP_DIR=$(mktemp -d -t bart-XXXXXXX)

    mkdir -p data

    # Create the center
    bart ones 2 $CENTER_SIZE $CENTER_SIZE $TMP_DIR/mask_center_new
    bart transpose 0 2 $TMP_DIR/mask_center_new $TMP_DIR/mask_center_new_transposed

    # Zero-pad the second (index 1) dimension to the full k-space dimension 
    bart resize -c 1 $Y 2 $Z $TMP_DIR/mask_center_new_transposed $TMP_DIR/mask_full_new

    # Create pattern with undersampling in phase and slice directions by R_Y and R_Z
    bart upat -Y $Y -Z $Z -y $R_Y -z $R_Z -c 1 $TMP_DIR/upat_new

    # Initialize the final combined pattern file
    bart saxpy 1 $TMP_DIR/mask_full_new $TMP_DIR/upat_new $TMP_DIR/upat_combined_new

    # Loop over N_ECHO times to apply shifts and join them
    for ((i=1; i<N_ECHO; i++)); do
        # Apply a circular shift of one along the phase direction
        bart circshift 1 $i $TMP_DIR/upat_new $TMP_DIR/upat_shifted_new

        # Combine the center mask and the shifted pattern
        bart saxpy 1 $TMP_DIR/mask_full_new $TMP_DIR/upat_shifted_new $TMP_DIR/tmp

        # Join the shifted pattern along the 5th dimension 
        bart join 5 $TMP_DIR/upat_combined_new $TMP_DIR/tmp $TMP_DIR/upat_combined_new
    done

    bart threshold -B 0.1 $TMP_DIR/upat_combined_new data/"$OUTPUT_NAME"

    # Clean up temporary directory
    rm -rf $TMP_DIR

    echo "Pattern creation completed. Output file: $OUTPUT_NAME"
}
EOF

# Make the script executable
chmod +x create_pattern.sh


In [95]:
%%bash
# Source the script to make the function available
source ./create_pattern.sh

# Parameters
R_Y=4        # Undersampling factor 4 leads to bad results
R_Z=1
Y=80       # Dimension Y
Z=16       # Dimension Z
N_ECHO=20  # Number of ECHO shifts
CENTER_SIZE=16

create_pattern -R_Y $R_Y -R_Z $R_Z -Y $Y -Z $Z -N_ECHO $N_ECHO -CENTER_SIZE $CENTER_SIZE -OUTPUT_NAME "upat_var"

Pattern creation completed. Output file: upat_var


In [96]:
upat_var = cfl.readcfl("data/upat_var")
interactive_bart_plot(upat_var) # it's a little hard to see ... echos are in dimension 5 

Output()

In [97]:
# Apply the mask
kSpace_upat_var = bart(1, 'fmac', upat_var, kSpace_transposed)
interactive_bart_plot(kSpace_upat_var)

Output()

In [98]:
bitmask = bartIO(0, 'bitmask 5')

REGULARIZATION = 10e-2
ITERATIONS=50

pics_upat_var = bart(1, f'pics -RI:{int(bitmask)}:{REGULARIZATION} -i{ITERATIONS} -S', kSpace_upat_var, ecalib_full)

Size: 2048000 Samples: 819199 Acc: 2.50
l1 regularization: 0.100000
Regularization terms: 1, Supporting variables: 0
FISTA
Total Time: 2.655738


In [99]:
R2_pics_upat_var = bart(1, 'mobafit -T', echo_times_final, pics_upat_var)

MAX_T2 = 1

T2_pics_upat_var = bart(1, 'invert', R2_pics_upat_var)

mask_pics_upat_var = bart(1, f'threshold -M {MAX_T2}', T2_pics_upat_var)

T2_pics_upat_var_masked = T2_pics_upat_var * mask_pics_upat_var

interactive_bart_plot(T2_pics_upat_var_masked, cmap='viridis') # Undersampling artifacts :(

Output()

## 4.0 Subspace Reco
First fully for testing

In [100]:
!bart signal -h

Usage: signal [-F] [-B] [-T] [-S] [-M] [-G] [-C] [--fat] [-I] [-s] [--short-TR-LL-approx] [-0 f:f:f] [-1 f:f:f] [-2 f:f:f] [-3 f:f:f] [-4 f:f:f] [-5 f:f:f] [-r f] [-e f] [-i f] [-f f] [-d f] [-t f] [-n d] [-b d] [--av-spokes d] [-m d] <basis-functions> 

Analytical simulation tool.

-F                      FLASH
-B                      bSSFP
-T                      TSE
-S                      SE
-M                      MOLLI
-G                      MGRE
-C                      IR MGRE
--fat                   Simulate additional fat component.
-I                      inversion recovery
-s                      inversion recovery starting from steady state
--short-TR-LL-approx    Short TR approximation for analytical LL model.
-0 min:max:N            range of off-resonance frequency [Hz]
-1 min:max:N            range of T1s [s]
-2 min:max:N            range of T2s [s]
-3 min:max:N            range of Mss
-4 min:max:N            range of T1 values for fat [s]
-5 min:max:N            range 

In [101]:
N_MEASUREMENTS = 20
MIN_T2 = 10e-3
MAX_T2 = 0.5
N_T2_POINTS = 1000
ECHO_TIME=10e-3

signal = bart(1, f'signal -n{N_MEASUREMENTS} -2 {MIN_T2}:{MAX_T2}:{N_T2_POINTS} -e{ECHO_TIME}')
#Should add a function for td plotting

#Formatting
signal = bart(1, f'transpose 2 5', signal)

signal = bart(1, f'squeeze', signal)

In [102]:
print(signal.shape)
interactive_bart_plot(signal)

(20, 1000)


Output()

In [103]:
U, S, V = bart(3, 'svd -e', signal)

# Extract coefficients
basis_tmp = bart(1, 'extract 1 0 3', U)
basis_tmp = bart(1, 'transpose 1 6', basis_tmp)
basis = bart(1, 'transpose 0 5', basis_tmp)

In [104]:
REGULARIZATION=3e-2
ITERATIONS=50

bitmask = bartIO(0, 'bitmask 5')

# Now we get a coefficient map
cfl.writecfl("data/basis", basis)
coeff_full = bart(1, f'pics -B data/basis -RI:{int(bitmask)}:{REGULARIZATION} -i{ITERATIONS} -S', kSpace_transposed, ecalib_full)

Basis: [ 80  80  16   1   1  20   3   1   1   1   1   1   1   1   1   1 ]
Max:   [ 80  80  16   1   1   1   3   1   1   1   1   1   1   1   1   1 ]
Size: 2048000 Samples: 2047999 Acc: 1.00
l1 regularization: 0.030000
Regularization terms: 1, Supporting variables: 0
FISTA
Total Time: 3.235034


In [107]:
# From the coefficients and the basis we can get the image
bitmask = int(bartIO(0, 'bitmask 6'))
              
img_subspace_full = bart(1, f'fmac -s {bitmask}', basis, coeff_full)

interactive_bart_plot(img_subspace_full)

Output()

In [108]:
# Now the pixelwise fit
R2_subspace_full = bart(1, 'mobafit -T', echo_times_final, img_subspace_full)

MAX_T2 = 1

T2_subspace_full = bart(1, 'invert', R2_subspace_full)

mask_subspace_full = bart(1, f'threshold -M {MAX_T2}', T2_subspace_full)

T2_subspace_full_masked = T2_subspace_full * mask_subspace_full

interactive_bart_plot(T2_subspace_full_masked, cmap='viridis') # Something is off with the scaling

Output()

## Two dim USP

In [109]:
%%bash
# Source the script to make the function available
source ./create_pattern.sh

# Parameters
R_Y=2      # Undersampling factor in the Y dimension
R_Z=2      # Undersampling factor in the Z dimension
Y=80       # Dimension Y
Z=16       # Dimension Z
N_ECHO=20  # Number of ECHO shifts
CENTER_SIZE=16

create_pattern -R_Y $R_Y -R_Z $R_Z -Y $Y -Z $Z -N_ECHO $N_ECHO -CENTER_SIZE $CENTER_SIZE -OUTPUT_NAME "upat_2x2"

Pattern creation completed. Output file: upat_2x2


In [110]:
upat_2x2 = cfl.readcfl("data/upat_2x2")
interactive_bart_plot(upat_2x2) 

Output()

In [111]:
#Apply the pattern
kSpace_2x2 = bart(1, 'fmac', upat_2x2, kSpace_transposed)
interactive_bart_plot(kSpace_2x2)

Output()

In [112]:
REGULARIZATION=3e-2
ITERATIONS=50

bitmask = bartIO(0, 'bitmask 5')

coeff_2x2 = bart(1, f'pics -B data/basis -RI:{int(bitmask)}:{REGULARIZATION} -i{ITERATIONS} -S', kSpace_2x2, ecalib_full)

Basis: [ 80  80  16   1   1  20   3   1   1   1   1   1   1   1   1   1 ]
Max:   [ 80  80  16   1   1   1   3   1   1   1   1   1   1   1   1   1 ]
Size: 2048000 Samples: 819199 Acc: 2.50
l1 regularization: 0.030000
Regularization terms: 1, Supporting variables: 0
FISTA
Total Time: 3.139522


In [113]:
# From the coefficients and the basis we can get the image
bitmask = int(bartIO(0, 'bitmask 6'))
              
img_2x2 = bart(1, f'fmac -s {bitmask}', basis, coeff_2x2)

interactive_bart_plot(img_2x2)

Output()

In [115]:
# Now the pixelwise fit
R2_2x2 = bart(1, 'mobafit -T', echo_times_final, img_2x2)

MAX_T2 = 1

T2_2x2 = bart(1, 'invert', R2_2x2)

mask_2x2 = bart(1, f'threshold -M {MAX_T2}', T2_2x2)

T2_2x2_masked = T2_2x2 * mask_2x2

interactive_bart_plot(T2_2x2_masked, cmap='viridis') # Something is off with the scaling

Output()